Preparations

In [32]:
from globals import *
DEFAULT_API_URL = "https://agents-course-unit4-scoring.hf.space"
api_url = DEFAULT_API_URL
questions_url = f"{api_url}/questions"
submit_url = f"{api_url}/submit"
file_url = f"{api_url}/files"

In [28]:
# get questions
response = requests.get(questions_url, timeout=15)
response.raise_for_status()
questions_data = response.json()

In [38]:
for item_num, item in enumerate(questions_data):
    # dict_keys(['task_id', 'question', 'Level', 'file_name'])
    # print(item['question'])
    # print('---')
    # print(f"{item['task_id']}")
    print(f"Task {item_num} has file: {item['file_name']}")
    # print(f"The question: \n {item['question']} \n")

Task 0 has file: 
Task 1 has file: 
Task 2 has file: 
Task 3 has file: cca530fc-4052-43b2-b130-b30968d8aa44.png
Task 4 has file: 
Task 5 has file: 
Task 6 has file: 
Task 7 has file: 
Task 8 has file: 
Task 9 has file: 99c9cc74-fdc8-46c6-8f8d-3ce2d3bfeea3.mp3
Task 10 has file: 
Task 11 has file: f918266a-b3e0-4914-865d-4faa564f1aef.py
Task 12 has file: 
Task 13 has file: 1f975693-876d-457b-a649-393859e79bf3.mp3
Task 14 has file: 
Task 15 has file: 
Task 16 has file: 
Task 17 has file: 
Task 18 has file: 7bd855d8-463d-4ed5-93ca-5fe35145f733.xlsx
Task 19 has file: 


In [22]:
train_dataset = load_dataset("gaia-benchmark/GAIA", '2023_level1', split="validation")
len(train_dataset)

53

In [25]:
print(train_dataset[0].keys())
item_0 = train_dataset[0]
# for item in train_dataset:
#     print(item)

dict_keys(['task_id', 'Question', 'Level', 'Final answer', 'file_name', 'file_path', 'Annotator Metadata'])


Simplest approach - just ask LLM

In [9]:
from globals import *
from tools import *

# ------------------------------------------------------ #
# MODELS & TOOLS
# ------------------------------------------------------ #
chat_llm = ChatTogether(model="meta-llama/Llama-3.3-70B-Instruct-Turbo-Free", api_key=os.getenv("TOGETHER_API_KEY"))

# ------------------------------------------------------ #
# STATE
# ------------------------------------------------------ #
class AgentState(TypedDict):
    # messages: list[AnyMessage, add_messages]
    messages: list[AnyMessage]
    # final_output_is_good: bool

# ------------------------------------------------------ #
# HELP FUNCTIONS
# ------------------------------------------------------ #
def step_print(state: AgentState, step_label: str):
    print(f'<<--- [{len(state["messages"])}] Starting {step_label}... --->>')

def messages_print(messages_to_print: List[AnyMessage]):
    print('--- Message/s ---')
    for m in messages_to_print:
        print(f'{m.type} ({m.name}): \n{m.content}')
    print(f'<<--- *** --->>')

# ------------------------------------------------------ #
# NODES
# ------------------------------------------------------ #
def preprocessing(state: AgentState):
    step_print(state, 'Preprocessing')
    messages_print(state['messages'][-1:])
    return {
        "messages": [SystemMessage(content=DEFAULT_SYSTEM_PROMPT)] + state["messages"]
    }


def assistant(state: AgentState):
    # state["messages"] = [SystemMessage(content=DEFAULT_SYSTEM_PROMPT)] + state["messages"]
    step_print(state, 'assistant')
    ai_message = chat_llm.invoke(state["messages"])
    messages_print([ai_message])
    return {
        'messages': state["messages"] + [ai_message]
    }


base_tool_node = ToolNode(tools)
def wrapped_tool_node(state: AgentState):
    step_print(state, 'Tools')
    # Call the original ToolNode
    result = base_tool_node.invoke(state)
    messages_print(result["messages"])
    # Append to the messages list instead of replacing it
    state["messages"] += result["messages"]
    return {"messages": state["messages"]}


# ------------------------------------------------------ #
# CONDITIONAL FUNCTIONS
# ------------------------------------------------------ #
def condition_tools_or_continue(
    state: Union[list[AnyMessage], dict[str, Any], BaseModel],
    messages_key: str = "messages",
) -> Literal["tools", "__end__"]:

    if isinstance(state, list):
        ai_message = state[-1]
    elif isinstance(state, dict) and (messages := state.get(messages_key, [])):
        ai_message = messages[-1]
    elif messages := getattr(state, messages_key, []):
        ai_message = messages[-1]
    else:
        raise ValueError(f"No messages found in input state to tool_edge: {state}")
    if hasattr(ai_message, "tool_calls") and len(ai_message.tool_calls) > 0:
        return "tools"
    # return "checker_final_answer"
    return "__end__"


# ------------------------------------------------------ #
# BUILDERS
# ------------------------------------------------------ #
def workflow_simple() -> Tuple[StateGraph, str]:
    i_builder = StateGraph(AgentState)
    # Nodes
    i_builder.add_node('preprocessing', preprocessing)
    i_builder.add_node('assistant', assistant)

    # Edges
    i_builder.add_edge(START, 'preprocessing')
    i_builder.add_edge('preprocessing', 'assistant')
    return i_builder, 'workflow_simple'


# ------------------------------------------------------ #
# COMPILATION
# ------------------------------------------------------ #
builder, builder_name = workflow_simple()
alfred = builder.compile()

In [10]:
response = alfred.invoke({'messages': [HumanMessage(content="If Eliud Kipchoge could maintain his record-making marathon pace indefinitely, how many thousand hours would it take him to run the distance between the Earth and the Moon its closest approach? Please use the minimum perigee value on the Wikipedia page for the Moon when carrying out your calculation. Round your result to the nearest 1000 hours and do not use any comma separators if necessary.")]})

<<--- [1] Starting Preprocessing... --->>
--- Message/s ---
human (None): 
If Eliud Kipchoge could maintain his record-making marathon pace indefinitely, how many thousand hours would it take him to run the distance between the Earth and the Moon its closest approach? Please use the minimum perigee value on the Wikipedia page for the Moon when carrying out your calculation. Round your result to the nearest 1000 hours and do not use any comma separators if necessary.
<<--- *** --->>
<<--- [2] Starting assistant... --->>
--- Message/s ---
ai (None): 
To calculate the time it would take Eliud Kipchoge to run from the Earth to the Moon at its closest approach, we first need to find out the distance between the Earth and the Moon at its closest approach and Eliud Kipchoge's speed.

The minimum perigee value for the Moon, according to Wikipedia, is approximately 356400 kilometers.

Eliud Kipchoge's record-making marathon pace is 2:01:39 hours for 42.195 kilometers. To find his speed in kilom

In [6]:
response1 = chat_llm.invoke([SystemMessage(content=DEFAULT_SYSTEM_PROMPT), HumanMessage(content="If Eliud Kipchoge could maintain his record-making marathon pace indefinitely, how many thousand hours would it take him to run the distance between the Earth and the Moon its closest approach? Please use the minimum perigee value on the Wikipedia page for the Moon when carrying out your calculation. Round your result to the nearest 1000 hours and do not use any comma separators if necessary.")])

In [8]:
response2 = chat_llm.invoke([SystemMessage(content=DEFAULT_SYSTEM_PROMPT), HumanMessage(content="If Eliud Kipchoge could maintain his record-making marathon pace indefinitely, how many thousand hours would it take him to run the distance between the Earth and the Moon its closest approach? Please use the minimum perigee value on the Wikipedia page for the Moon when carrying out your calculation. Round your result to the nearest 1000 hours and do not use any comma separators if necessary."), response1])